In [2]:
import pandas as pd
from surprise import Reader
from surprise import Dataset as ds
import numpy as np
from sklearn.model_selection import train_test_split 
from surprise import SVD
from sklearn import svm
from sklearn.decomposition import PCA
from surprise.model_selection import cross_validate
import matplotlib.pyplot as plt
import sklearn.metrics as metrics
from sklearn.neighbors import NearestNeighbors
from sklearn.metrics.pairwise import pairwise_distances
import warnings
warnings.filterwarnings('ignore')
import re
import seaborn as sns
from surprise import SVD, accuracy
from surprise.model_selection import train_test_split, GridSearchCV


# Reading the data

In [32]:
ratings = pd.read_csv('../data/ratings.csv', index_col=0)
ratings.shape

(100282, 14)

In [88]:
subset = ratings[:10].copy()
# subset

In [90]:
# subset = ratings[:10].copy()
hidden = {}
for idx, row in ratings.iterrows():
    if (row.values !=0).sum() >1:
        colmax= row.idxmax() 
        row[colmax]= 0
        prod = [colmax]
        hidden[idx]= prod
hidden
# ratings.head()

{294: ['DENTAL_DAILIES_ITEMS'],
 1737: ['YAKER_TREATS_ITEMS'],
 3127: ['DENTAL_DAILIES_ITEMS'],
 4695: ['DENTAL_DAILIES_ITEMS'],
 11844: ['SALMON_TREATS_ITEMS'],
 12111: ['CHICKEN_TREATS_ITEMS'],
 12323: ['PORK_TREATS_ITEMS'],
 18158: ['DENTAL_DAILIES_ITEMS'],
 31145: ['YAKER_TREATS_ITEMS'],
 32549: ['DENTAL_DAILIES_ITEMS'],
 33161: ['YAKER_TREATS_ITEMS'],
 36749: ['SALMON_TREATS_ITEMS'],
 39096: ['DUCK_TREATS_ITEMS'],
 40090: ['DUCK_TREATS_ITEMS'],
 41711: ['DENTAL_DAILIES_ITEMS'],
 43076: ['DENTAL_DAILIES_ITEMS'],
 43265: ['DENTAL_DAILIES_ITEMS'],
 53518: ['SUPER_SALMON_TREATS_ITEMS'],
 54782: ['DENTAL_DAILIES_ITEMS'],
 59214: ['DENTAL_DAILIES_ITEMS'],
 61106: ['SUPER_SALMON_TREATS_ITEMS'],
 63330: ['GOOD_DOG_TREATS_ITEMS'],
 65730: ['DENTAL_DAILIES_ITEMS'],
 67695: ['DENTAL_DAILIES_ITEMS'],
 69073: ['DENTAL_DAILIES_ITEMS'],
 71287: ['DENTAL_DAILIES_ITEMS'],
 72289: ['DENTAL_DAILIES_ITEMS'],
 73893: ['SUPER_LAMB_TREATS_ITEMS'],
 78422: ['DUCK_TREATS_ITEMS'],
 85594: ['DENTAL_DAILIES_

In [64]:
# Reading the ratings matrix
ratings = new_df
new_df.shape
# new_df.head()

(100282, 14)

# building the rating column

In [91]:
DF = pd.DataFrame()
for key in new_df.keys():
    df = pd.DataFrame(columns=[ 'Item', 'ratings'])
    df['Rating'] = pd.Series(new_df[key])
    df['ratings'] = pd.DataFrame(new_df[key])
    df['Item'] = key#pd.DataFrame(df.columns)
    df['User'] = pd.DataFrame(df.index)

    DF = pd.concat([DF, df], axis = 0)
DF.head()


Item  ratings  Rating       User
CUSTOMER_ID                                                
294          YAKER_TREATS_ITEMS        0       0   459693.0
1737         YAKER_TREATS_ITEMS        0       0  2802670.0
3127         YAKER_TREATS_ITEMS        1       1  3095470.0
4695         YAKER_TREATS_ITEMS        1       1  3126721.0
5549         YAKER_TREATS_ITEMS        0       0  3142994.0

In [92]:
#Removing CUSTOMER_ID as index
df=DF.reset_index()
df.head()

CUSTOMER_ID                Item  ratings  Rating       User
0          294  YAKER_TREATS_ITEMS        0       0   459693.0
1         1737  YAKER_TREATS_ITEMS        0       0  2802670.0
2         3127  YAKER_TREATS_ITEMS        1       1  3095470.0
3         4695  YAKER_TREATS_ITEMS        1       1  3126721.0
4         5549  YAKER_TREATS_ITEMS        0       0  3142994.0

In [93]:
# converting CUSTOMER_ID from integer to string
df['CUSTOMER_ID'] = df['CUSTOMER_ID'].apply(str)
#df.isnull().sum()


In [94]:
df.CUSTOMER_ID = df.CUSTOMER_ID.astype('str')
df.Item = df.Item.astype('str')

# Transforming the pandas dataframe into surprise dataframe 

In [100]:
from surprise import Reader, Dataset
reader = Reader()
data = Dataset.load_from_df(df[['CUSTOMER_ID', 'Item', 'ratings']], reader)

# Sliptting the data into train and test

In [106]:
# taking 20% of data for test and 80% of data for train
trainset, testset = train_test_split(data, test_size=0.2)

# Applying the Singular Value Decomposition model

In [105]:
from surprise import SVD, accuracy
algo = SVD()
algo.fit(trainset)

predictions = algo.test(trainset)

TypeError: 'Trainset' object is not iterable

In [ ]:
# predictions
iterator = trainset.all_ratings()
new_df = pd.DataFrame(columns=['uid', 'iid', 'rating'])
i = 0
for (uid, iid, rating) in iterator:
    new_df.loc[i] = [uid, iid, rating]
    i = i+1

new_df.head(2)

# Computing the Root Mean Square Error

In [25]:
from surprise import accuracy
error=accuracy.rmse(predictions)
print("Accuracy: {:.4f}".format(100-error))

RMSE: 1.2656
Accuracy: 98.7344


# Building the recommendation

In [28]:
from collections import defaultdict
def get_top_n(predictions, n=5):
    # First map the predictions to each user.
    top_n = defaultdict(list)
    for uid, iid, true_r, est, _ in predictions:
        top_n[uid].append((iid, est))

    # Then sort the predictions for each user and retrieve the k highest ones.
    for uid, user_ratings in top_n.items():
        user_ratings.sort(key=lambda x: x[1], reverse=True)
        top_n[uid] = user_ratings[:n]
    return top_n

# #Top 5 recommendations per customer

In [29]:
top_n = get_top_n(predictions, n=5)
top_n['3127']

[('DENTAL_DAILIES_ITEMS', 2.157933250665788),
 ('YAKER_TREATS_ITEMS', 1),
 ('WHIMZEES_BONE_TREATS_ITEMS', 1),
 ('LAMB_TREATS_ITEMS', 1),
 ('SUPER_DUCK_TREATS_ITEMS', 1)]

In [30]:
# Print the recommended items for each user
for uid, user_ratings in top_n.items():
    print(uid, [iid for (iid, _) in user_ratings])

5483402 ['GOOD_DOG_TREATS_ITEMS', 'SUPER_DUCK_TREATS_ITEMS', 'SALMON_TREATS_ITEMS']
4575414 ['DENTAL_DAILIES_ITEMS', 'WHIMZEES_BONE_TREATS_ITEMS', 'SUPER_LAMB_TREATS_ITEMS', 'SALMON_TREATS_ITEMS', 'SUPER_SALMON_TREATS_ITEMS']
3233412 ['DENTAL_DAILIES_ITEMS', 'SUPER_SALMON_TREATS_ITEMS']
4541201 ['GOOD_DOG_TREATS_ITEMS', 'COLD_PRESSED_DUCK_TREATS_ITEMS']
3237306 ['GOOD_DOG_TREATS_ITEMS', 'LAMB_TREATS_ITEMS', 'WHIMZEES_TREATS_ITEMS', 'SUPER_DUCK_TREATS_ITEMS', 'SUPER_SALMON_TREATS_ITEMS']
6117828 ['DENTAL_DAILIES_ITEMS', 'DUCK_TREATS_ITEMS', 'GOOD_DOG_TREATS_ITEMS', 'SALMON_TREATS_ITEMS', 'SUPER_DUCK_TREATS_ITEMS']
4620946 ['GOOD_DOG_TREATS_ITEMS', 'SUPER_SALMON_TREATS_ITEMS', 'SALMON_TREATS_ITEMS']
5658828 ['DENTAL_DAILIES_ITEMS', 'CHICKEN_TREATS_ITEMS', 'WHIMZEES_BONE_TREATS_ITEMS']
3184096 ['YAKER_TREATS_ITEMS', 'SALMON_TREATS_ITEMS', 'CHICKEN_TREATS_ITEMS']
3553989 ['WHIMZEES_TREATS_ITEMS', 'CHICKEN_TREATS_ITEMS', 'YAKER_TREATS_ITEMS', 'PORK_TREATS_ITEMS', 'SUPER_LAMB_TREATS_ITEMS']


3930609 ['YAKER_TREATS_ITEMS', 'SUPER_DUCK_TREATS_ITEMS', 'SUPER_LAMB_TREATS_ITEMS']
3793920 ['DENTAL_DAILIES_ITEMS', 'GOOD_DOG_TREATS_ITEMS', 'COLD_PRESSED_DUCK_TREATS_ITEMS', 'WHIMZEES_BONE_TREATS_ITEMS', 'PORK_TREATS_ITEMS']
3175836 ['DENTAL_DAILIES_ITEMS', 'SUPER_SALMON_TREATS_ITEMS', 'WHIMZEES_BONE_TREATS_ITEMS']
3949046 ['SUPER_LAMB_TREATS_ITEMS', 'YAKER_TREATS_ITEMS']
4502318 ['SUPER_LAMB_TREATS_ITEMS', 'SALMON_TREATS_ITEMS']
4393626 ['DENTAL_DAILIES_ITEMS', 'WHIMZEES_TREATS_ITEMS', 'SUPER_SALMON_TREATS_ITEMS', 'COLD_PRESSED_DUCK_TREATS_ITEMS', 'SUPER_LAMB_TREATS_ITEMS']
4413241 ['GOOD_DOG_TREATS_ITEMS', 'SUPER_DUCK_TREATS_ITEMS']
4369796 ['GOOD_DOG_TREATS_ITEMS', 'SUPER_SALMON_TREATS_ITEMS', 'COLD_PRESSED_DUCK_TREATS_ITEMS', 'SUPER_LAMB_TREATS_ITEMS', 'WHIMZEES_TREATS_ITEMS']
4272998 ['YAKER_TREATS_ITEMS', 'COLD_PRESSED_DUCK_TREATS_ITEMS', 'WHIMZEES_BONE_TREATS_ITEMS', 'SUPER_DUCK_TREATS_ITEMS', 'PORK_TREATS_ITEMS']
4796015 ['WHIMZEES_BONE_TREATS_ITEMS', 'CHICKEN_TREATS_ITEMS',

5789124 ['SUPER_SALMON_TREATS_ITEMS', 'PORK_TREATS_ITEMS']
5647925 ['SUPER_DUCK_TREATS_ITEMS', 'PORK_TREATS_ITEMS', 'CHICKEN_TREATS_ITEMS', 'SALMON_TREATS_ITEMS', 'SUPER_LAMB_TREATS_ITEMS']
5845390 ['GOOD_DOG_TREATS_ITEMS', 'SALMON_TREATS_ITEMS', 'YAKER_TREATS_ITEMS', 'WHIMZEES_BONE_TREATS_ITEMS', 'PORK_TREATS_ITEMS']
5148376 ['SUPER_SALMON_TREATS_ITEMS']
3286210 ['GOOD_DOG_TREATS_ITEMS', 'WHIMZEES_BONE_TREATS_ITEMS', 'LAMB_TREATS_ITEMS', 'YAKER_TREATS_ITEMS']
3457846 ['WHIMZEES_BONE_TREATS_ITEMS', 'SUPER_SALMON_TREATS_ITEMS', 'PORK_TREATS_ITEMS', 'LAMB_TREATS_ITEMS']
5992244 ['DENTAL_DAILIES_ITEMS', 'WHIMZEES_BONE_TREATS_ITEMS']
4038294 ['WHIMZEES_TREATS_ITEMS', 'CHICKEN_TREATS_ITEMS']
5649414 ['PORK_TREATS_ITEMS', 'WHIMZEES_BONE_TREATS_ITEMS', 'COLD_PRESSED_DUCK_TREATS_ITEMS']
5769287 ['YAKER_TREATS_ITEMS', 'DUCK_TREATS_ITEMS', 'WHIMZEES_TREATS_ITEMS', 'WHIMZEES_BONE_TREATS_ITEMS']
5531932 ['PORK_TREATS_ITEMS', 'WHIMZEES_TREATS_ITEMS', 'WHIMZEES_BONE_TREATS_ITEMS']
4070590 ['SUPER_LA

5390159 ['DUCK_TREATS_ITEMS', 'COLD_PRESSED_DUCK_TREATS_ITEMS', 'SUPER_DUCK_TREATS_ITEMS']
4877873 ['CHICKEN_TREATS_ITEMS', 'SUPER_LAMB_TREATS_ITEMS']
3143531 ['CHICKEN_TREATS_ITEMS', 'WHIMZEES_TREATS_ITEMS', 'PORK_TREATS_ITEMS', 'SUPER_LAMB_TREATS_ITEMS', 'LAMB_TREATS_ITEMS']
3970434 ['YAKER_TREATS_ITEMS', 'LAMB_TREATS_ITEMS', 'COLD_PRESSED_DUCK_TREATS_ITEMS', 'WHIMZEES_TREATS_ITEMS', 'SUPER_LAMB_TREATS_ITEMS']
3256378 ['GOOD_DOG_TREATS_ITEMS', 'SUPER_SALMON_TREATS_ITEMS', 'WHIMZEES_BONE_TREATS_ITEMS', 'SUPER_LAMB_TREATS_ITEMS', 'DUCK_TREATS_ITEMS']
4660026 ['SALMON_TREATS_ITEMS', 'COLD_PRESSED_DUCK_TREATS_ITEMS', 'WHIMZEES_BONE_TREATS_ITEMS', 'LAMB_TREATS_ITEMS', 'YAKER_TREATS_ITEMS']
6189626 ['DENTAL_DAILIES_ITEMS', 'YAKER_TREATS_ITEMS', 'WHIMZEES_TREATS_ITEMS', 'SUPER_LAMB_TREATS_ITEMS', 'SUPER_SALMON_TREATS_ITEMS']
3488513 ['WHIMZEES_TREATS_ITEMS', 'WHIMZEES_BONE_TREATS_ITEMS', 'DUCK_TREATS_ITEMS', 'CHICKEN_TREATS_ITEMS']
5217353 ['LAMB_TREATS_ITEMS', 'SUPER_LAMB_TREATS_ITEMS', 'W

2742627 ['GOOD_DOG_TREATS_ITEMS', 'COLD_PRESSED_DUCK_TREATS_ITEMS', 'SUPER_DUCK_TREATS_ITEMS', 'PORK_TREATS_ITEMS', 'DUCK_TREATS_ITEMS']
3606099 ['DENTAL_DAILIES_ITEMS', 'PORK_TREATS_ITEMS', 'WHIMZEES_BONE_TREATS_ITEMS']
6257836 ['DENTAL_DAILIES_ITEMS', 'DUCK_TREATS_ITEMS', 'SALMON_TREATS_ITEMS', 'YAKER_TREATS_ITEMS', 'WHIMZEES_TREATS_ITEMS']
5434423 ['DENTAL_DAILIES_ITEMS', 'PORK_TREATS_ITEMS', 'GOOD_DOG_TREATS_ITEMS', 'WHIMZEES_BONE_TREATS_ITEMS', 'LAMB_TREATS_ITEMS']
5856881 ['YAKER_TREATS_ITEMS', 'SUPER_DUCK_TREATS_ITEMS', 'WHIMZEES_BONE_TREATS_ITEMS', 'LAMB_TREATS_ITEMS', 'SALMON_TREATS_ITEMS']
3131213 ['YAKER_TREATS_ITEMS', 'CHICKEN_TREATS_ITEMS', 'WHIMZEES_TREATS_ITEMS', 'LAMB_TREATS_ITEMS']
3262100 ['SUPER_SALMON_TREATS_ITEMS', 'WHIMZEES_BONE_TREATS_ITEMS', 'SUPER_DUCK_TREATS_ITEMS', 'COLD_PRESSED_DUCK_TREATS_ITEMS']
5312605 ['DENTAL_DAILIES_ITEMS', 'COLD_PRESSED_DUCK_TREATS_ITEMS', 'SUPER_LAMB_TREATS_ITEMS', 'SUPER_SALMON_TREATS_ITEMS']
4994015 ['SALMON_TREATS_ITEMS', 'COLD_PR

...

5187301 ['SALMON_TREATS_ITEMS']
4117719 ['WHIMZEES_BONE_TREATS_ITEMS']
5735921 ['DUCK_TREATS_ITEMS', 'LAMB_TREATS_ITEMS']
3951802 ['COLD_PRESSED_DUCK_TREATS_ITEMS']
5671623 ['WHIMZEES_TREATS_ITEMS']
5932074 ['WHIMZEES_TREATS_ITEMS']
3124876 ['SUPER_LAMB_TREATS_ITEMS']
5406132 ['COLD_PRESSED_DUCK_TREATS_ITEMS']
3845376 ['WHIMZEES_TREATS_ITEMS']
5380915 ['DENTAL_DAILIES_ITEMS', 'DUCK_TREATS_ITEMS']
4673568 ['WHIMZEES_BONE_TREATS_ITEMS']
4827242 ['WHIMZEES_BONE_TREATS_ITEMS', 'SUPER_LAMB_TREATS_ITEMS', 'LAMB_TREATS_ITEMS']
6173191 ['YAKER_TREATS_ITEMS']
3764549 ['SUPER_LAMB_TREATS_ITEMS']
4710897 ['SUPER_DUCK_TREATS_ITEMS']
4590886 ['GOOD_DOG_TREATS_ITEMS']
5293348 ['LAMB_TREATS_ITEMS']
5582201 ['SUPER_DUCK_TREATS_ITEMS', 'PORK_TREATS_ITEMS']
3181817 ['CHICKEN_TREATS_ITEMS']
3576083 ['CHICKEN_TREATS_ITEMS']
3140134 ['SUPER_LAMB_TREATS_ITEMS']
3608831 ['COLD_PRESSED_DUCK_TREATS_ITEMS']
4780725 ['COLD_PRESSED_DUCK_TREATS_ITEMS']
4822394 ['SALMON_TREATS_ITEMS']
4246605 ['WHIMZEES_TREATS_ITEM

5428334 ['CHICKEN_TREATS_ITEMS', 'SUPER_LAMB_TREATS_ITEMS']
5959960 ['GOOD_DOG_TREATS_ITEMS']
3132550 ['CHICKEN_TREATS_ITEMS']
3838884 ['PORK_TREATS_ITEMS']
4876460 ['YAKER_TREATS_ITEMS']
3300312 ['DUCK_TREATS_ITEMS']
5399797 ['WHIMZEES_BONE_TREATS_ITEMS', 'LAMB_TREATS_ITEMS']
3123240 ['DENTAL_DAILIES_ITEMS', 'PORK_TREATS_ITEMS']
3781940 ['YAKER_TREATS_ITEMS']
4847180 ['WHIMZEES_TREATS_ITEMS']
3166213 ['SUPER_LAMB_TREATS_ITEMS', 'PORK_TREATS_ITEMS']
5741677 ['DUCK_TREATS_ITEMS']
4581949 ['GOOD_DOG_TREATS_ITEMS']
5018832 ['CHICKEN_TREATS_ITEMS', 'YAKER_TREATS_ITEMS']
4757230 ['COLD_PRESSED_DUCK_TREATS_ITEMS']
3389234 ['GOOD_DOG_TREATS_ITEMS']
3890418 ['SUPER_LAMB_TREATS_ITEMS']
4976071 ['SUPER_DUCK_TREATS_ITEMS']
5409682 ['SUPER_LAMB_TREATS_ITEMS', 'WHIMZEES_TREATS_ITEMS']
4548570 ['SUPER_SALMON_TREATS_ITEMS']
3457591 ['DENTAL_DAILIES_ITEMS']
3829577 ['WHIMZEES_TREATS_ITEMS']
5452741 ['DUCK_TREATS_ITEMS']
5278885 ['WHIMZEES_BONE_TREATS_ITEMS']
3662772 ['COLD_PRESSED_DUCK_TREATS_ITEMS']


3125367 ['GOOD_DOG_TREATS_ITEMS', 'SALMON_TREATS_ITEMS']
5392759 ['PORK_TREATS_ITEMS']
590960 ['GOOD_DOG_TREATS_ITEMS', 'SUPER_DUCK_TREATS_ITEMS']
5614688 ['DENTAL_DAILIES_ITEMS']
3824080 ['WHIMZEES_BONE_TREATS_ITEMS']
5144267 ['DUCK_TREATS_ITEMS']
5574760 ['CHICKEN_TREATS_ITEMS']
4595655 ['SALMON_TREATS_ITEMS']
3522855 ['PORK_TREATS_ITEMS']
3538500 ['YAKER_TREATS_ITEMS']
3097988 ['DENTAL_DAILIES_ITEMS']
5353598 ['DENTAL_DAILIES_ITEMS']
4319019 ['SALMON_TREATS_ITEMS']
5535006 ['SUPER_LAMB_TREATS_ITEMS']
3465127 ['SUPER_LAMB_TREATS_ITEMS']
5233840 ['PORK_TREATS_ITEMS']
3189699 ['SUPER_DUCK_TREATS_ITEMS']
3320440 ['WHIMZEES_TREATS_ITEMS', 'PORK_TREATS_ITEMS']
3379858 ['SALMON_TREATS_ITEMS']
3569317 ['GOOD_DOG_TREATS_ITEMS']
4794473 ['SALMON_TREATS_ITEMS']
5230003 ['DENTAL_DAILIES_ITEMS']
3794716 ['DENTAL_DAILIES_ITEMS']
4702134 ['SUPER_SALMON_TREATS_ITEMS']
3429810 ['LAMB_TREATS_ITEMS']
6072742 ['CHICKEN_TREATS_ITEMS']
3593290 ['LAMB_TREATS_ITEMS']
3180268 ['SUPER_LAMB_TREATS_ITEMS', 'SU

5936963 ['DUCK_TREATS_ITEMS']
4942009 ['LAMB_TREATS_ITEMS']
5263813 ['WHIMZEES_TREATS_ITEMS']
3058718 ['COLD_PRESSED_DUCK_TREATS_ITEMS', 'LAMB_TREATS_ITEMS']
4075312 ['WHIMZEES_TREATS_ITEMS']
5170732 ['COLD_PRESSED_DUCK_TREATS_ITEMS']
3787567 ['CHICKEN_TREATS_ITEMS']
3351255 ['PORK_TREATS_ITEMS']
6181086 ['PORK_TREATS_ITEMS']
5366434 ['LAMB_TREATS_ITEMS']
5970039 ['SUPER_LAMB_TREATS_ITEMS']
4784489 ['DUCK_TREATS_ITEMS']
5313749 ['CHICKEN_TREATS_ITEMS']
4772232 ['YAKER_TREATS_ITEMS']
5561275 ['GOOD_DOG_TREATS_ITEMS']
3811772 ['DUCK_TREATS_ITEMS']
5852350 ['LAMB_TREATS_ITEMS']
4091516 ['WHIMZEES_BONE_TREATS_ITEMS']
5382505 ['SUPER_LAMB_TREATS_ITEMS']
6218863 ['SUPER_SALMON_TREATS_ITEMS']
3381401 ['DENTAL_DAILIES_ITEMS']
5019314 ['LAMB_TREATS_ITEMS']
3828844 ['SUPER_LAMB_TREATS_ITEMS']
5922146 ['SUPER_SALMON_TREATS_ITEMS']
3366467 ['PORK_TREATS_ITEMS']
3400448 ['SUPER_DUCK_TREATS_ITEMS']
3598026 ['SALMON_TREATS_ITEMS']
4457174 ['YAKER_TREATS_ITEMS']
4319457 ['SUPER_LAMB_TREATS_ITEMS']
168

6087296 ['WHIMZEES_BONE_TREATS_ITEMS']
6263803 ['SUPER_DUCK_TREATS_ITEMS']
3256928 ['DUCK_TREATS_ITEMS']
4535236 ['SUPER_SALMON_TREATS_ITEMS']
4251679 ['COLD_PRESSED_DUCK_TREATS_ITEMS']
5956720 ['PORK_TREATS_ITEMS']
5509734 ['DENTAL_DAILIES_ITEMS']
5380930 ['SUPER_LAMB_TREATS_ITEMS']
6202176 ['CHICKEN_TREATS_ITEMS']
5537947 ['WHIMZEES_TREATS_ITEMS']
5960975 ['PORK_TREATS_ITEMS']
3138239 ['SALMON_TREATS_ITEMS']
4928662 ['SALMON_TREATS_ITEMS']
5913532 ['GOOD_DOG_TREATS_ITEMS', 'CHICKEN_TREATS_ITEMS']
4305928 ['LAMB_TREATS_ITEMS']
3650864 ['DENTAL_DAILIES_ITEMS']
5504166 ['WHIMZEES_TREATS_ITEMS']
3133301 ['SUPER_SALMON_TREATS_ITEMS']
4733401 ['PORK_TREATS_ITEMS']
5644828 ['WHIMZEES_BONE_TREATS_ITEMS']
4319398 ['SUPER_DUCK_TREATS_ITEMS']
3688355 ['DUCK_TREATS_ITEMS']
5538875 ['YAKER_TREATS_ITEMS']
3192367 ['COLD_PRESSED_DUCK_TREATS_ITEMS']
4715650 ['SUPER_LAMB_TREATS_ITEMS']
3176173 ['WHIMZEES_BONE_TREATS_ITEMS']
6136310 ['DENTAL_DAILIES_ITEMS']
4459496 ['SUPER_LAMB_TREATS_ITEMS']
3203718 